In [67]:
import pandas as pd
import numpy as np
import hvplot.pandas  # noqa
import matplotlib.pyplot as plt
import logging
import copy
from scipy.optimize import curve_fit
from sklearn.metrics import r2_score

import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px

# import lab_tools
import pickle
logging.basicConfig(level=logging.INFO)
import math
from scipy.constants import mu_0 as mu_0
from uncertainties import ufloat
import uncertainties
from uncertainties.umath import *
from uncertainties import unumpy
from matplotlib import pyplot
import os
from collections import OrderedDict
import plotly.express as px

def uplot(x_ufloats, y_ufloats, ax=plt, **kwargs):
    getattr(ax, 'errorbar')
    plt.errorbar( unumpy.nominal_values(x_ufloats), unumpy.nominal_values(y_ufloats),
      xerr=unumpy.std_devs(x_ufloats), yerr= unumpy.std_devs(y_ufloats),ecolor='green',barsabove=True, **kwargs )


def load_pickle(name):
    with open(os.path.join('pickles',f'{name}.pickle'), 'rb') as handle:
        return pickle.load(handle)

def save_pickle(name, pick):
    if not os.path.exists('pickles'):
        os.makedirs('pickles')
    with open(os.path.join('pickles',f'{name}.pickle'), 'wb') as handle:
        return pickle.dump(pick,handle)

def load_state(state = 'state'):
    globals().update(load_pickle(state))

def save_state():
    data = {k:v for k,v in globals().items() if not k.startswith('_')}
    print(data)
    save_pickle('state', {k:v for k,v in globals().items() if not k.startswith('_')})

def malus_fit(x, a, b):
    return a * np.cos(x - b)**2

def clean_errors(df):
    return df.applymap(unumpy.nominal_values)

def to_matlab(df, name):
    df.applymap(unumpy.nominal_values).to_csv(f'{name}.csv', index=False)


def genrate_fit_data(df, col, addition=10):
    max = unumpy.nominal_values(df[col].max())
    min = unumpy.nominal_values(df[col].min())
    return np.linspace(min - addition, max + addition, 100)


def read_to_dict(folder):
    csv_files = os.listdir(folder)
    data_dict = {}
    for x in csv_files:
        path = os.path.join(folder, x)
        try:
            data_dict[os.path.splitext(os.path.basename(path))[0]] = load_data(path)
        except:
            print(f"Error reading file {path}")

    return data_dict

def load_data(path):
    df = pd.read_excel(path, header=None, names=['t', 'p'], skiprows=6)
    return df

def drop(df, col, n):
    largest = df.nlargest(n, col).index.to_list()
    smallest = df.nsmallest(n, col).index.to_list()
    indexces = largest + smallest
    return df.drop(indexces)

def get_min_max_error(df, col):
    max = df[col].max()
    min = df[col].min()
    return (max - min)

def puplot(x_ufloats, y_ufloats, **kwargs):

    # del fig

    df_ = pd.DataFrame({
        'x': unumpy.nominal_values(x_ufloats),
        'y': unumpy.nominal_values(y_ufloats),
        'x_err': unumpy.std_devs(x_ufloats),
        'y_err': unumpy.std_devs(y_ufloats)
        })

    fig = px.scatter(df_, x="x", y="y",
                 error_x="x_err", error_y="y_err")
    fig.show()
    # return fig

def rad2deg(v):
    return v * 180 / np.pi

def deg2rad(v):
    return v * np.pi / 180

In [68]:
l = ufloat(15,0.5)
l = l/10
m_g = ufloat(17.4,0.1)
m_f = ufloat(17.3,0.1)
v_g = ufloat(180,5)
v_f = ufloat(150,5)
v_tot = v_g + v_f

In [69]:
pd.set_option("display.precision", 9)

In [70]:
chem_react = pd.read_excel(r'data/chemical_reaction/chirality.xlsx', header=None, names=['t', 'p'], skiprows=6)

In [71]:
Dimentionless_Transmition = chem_react['p']/0.000146
time = chem_react['t']/60

In [72]:
phi = np.arccos((Dimentionless_Transmition)**0.5)
phi = phi * 180/np.pi

In [73]:
px.scatter(x=time, y=phi)


In [74]:
C_g = phi/(l*52.2)
C_f = phi/(l*(-92.4))
puplot(time,C_g)


In [75]:
ind = np.where(time == 10.30514)


0         0.000000000
1         0.001816773
2         0.003616873
3         0.005566986
4         0.006767054
             ...     
11956    21.715108701
11957    21.717008809
11958    21.718542230
11959    21.720075651
11960    21.721625741
Name: t, Length: 11961, dtype: float64

In [76]:
new_time = time[:5996]
new_Cg = C_g[:5996]
puplot(time[:5996],C_g[:5996])


In [77]:
new_Cg


0       0.362+/-0.012
1       0.357+/-0.012
2       0.351+/-0.012
3       0.349+/-0.012
4       0.349+/-0.012
            ...      
5991    0.196+/-0.007
5992    0.196+/-0.007
5993    0.199+/-0.007
5994    0.201+/-0.007
5995    0.204+/-0.007
Name: p, Length: 5996, dtype: object

In [78]:
puplot(new_time,new_Cg)
